In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs
import numpy as np

# set the following to True when connected to hardware:
run_on_hw = False

# instantiate channels representing two AWGs and two digitizers
awgs = qcs.Channels(range(2), "readoutawg")
digs = qcs.Channels(range(2), "readoutreceiver")

# load our channel mapper to connect the virtual channels above to physical ones
mapper = qcs.load("../../assets/channel_mapper.qcs")

In [3]:
# define the frequency and amplitude of our RF waveform as QCS variables
frequency = qcs.Scalar("rf", dtype=float)
amplitude = qcs.Scalar("amp", dtype=float, value=1)


def make_program():
    """Creates a simple program with a single RF waveform"""
    program = qcs.Program()
    # define the waveform using this frequency variable & add it to the program
    gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, frequency)
    program.add_waveform(gauss, awgs)

    # define an integration filter using the same RF waveform but with fixed frequency
    int_filter = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, 4.15e9)
    program.add_acquisition(int_filter, digs)

    # specify the number of shots
    return program.n_shots(10)


program = make_program()

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# add the sweep, targeting the `frequency` variable
program.sweep(frequencies, frequency)

program.draw()

In [4]:
print(program.repetitions.items)

[Sweep(rf=Array(name=frequencies, shape=(5,), dtype=float, unit=none)), Repeat(10)]


In [5]:
if run_on_hw:
    # initialize the backend pass
    backend = qcs.HclBackend(channel_mapper=mapper)
    # the executor returns the program populated with results
    program = qcs.Executor(backend).execute(program)
    # (optional) export the data to an HDF5 file
    program.to_hdf5("program2.hdf5")

# we are loading a previously run program here for this example
program = qcs.load("program2.hdf5")

In [6]:
program.plot_trace()

In [7]:
program.get_iq_pandas(stack_channels=True)

(rf, 4.05 GHz)                      \
                                          0                   1   
(((readoutreceiver_0)))  0.002351-0.002617j  0.001562-0.003162j   
(((readoutreceiver_1))) -0.003926-0.002629j -0.002427-0.001740j   
(((readoutreceiver_2)))  0.004186-0.001393j  0.004653-0.001658j   
(((readoutreceiver_3)))  0.003129+0.001425j  0.003441+0.001442j   

                                                                 \
                                          2                   3   
(((readoutreceiver_0)))  0.001999-0.003444j  0.002334-0.002812j   
(((readoutreceiver_1))) -0.002129-0.000508j -0.003600-0.001572j   
(((readoutreceiver_2)))  0.004354-0.000896j  0.004046-0.001135j   
(((readoutreceiver_3)))  0.002865+0.002030j  0.003196+0.001574j   

                                                                 \
                                          4                   5   
(((readoutreceiver_0)))  0.001619-0.003178j  0.001974-0.003325j   
(((readoutreceiver_1))) -0.002188-0.001321j -0.001880-0.000612j   
(((readoutreceiver_2)))  0.004784-0.001412j  0.004066-0.000832j   
(((readoutreceiver_3)))  0.003758+0.001457j  0.003232+0.002031j   

                                                                 \
                                          6                   7   
(((readoutreceiver_0)))  0.002244-0.002614j  0.001584-0.003135j   
(((readoutreceiver_1))) -0.004357-0.002121j -0.002159-0.002206j   
(((readoutreceiver_2)))  0.003935-0.001297j  0.004887-0.001311j   
(((readoutreceiver_3)))  0.002919+0.001560j  0.003477+0.001332j   

                                                                 ...  \
                                          8                   9  ...   
(((readoutreceiver_0)))  0.001894-0.003386j  0.002325-0.002754j  ...   
(((readoutreceiver_1))) -0.002250-0.000615j -0.004123-0.002111j  ...   
(((readoutreceiver_2)))  0.004025-0.000916j  0.004254-0.001515j  ...   
(((readoutreceiver_3)))  0.002991+0.002071j  0.003148+0.001320j  ...   

                             (rf, 4.25 GHz)                      \
                                          0                   1   
(((readoutreceiver_0))) -0.000353-0.000242j -0.000056+0.000357j   
(((readoutreceiver_1)))  0.000047-0.000634j -0.000227+0.000729j   
(((readoutreceiver_2)))  0.000401-0.000258j -0.000200-0.000369j   
(((readoutreceiver_3))) -0.000067+0.000023j -0.000269-0.000081j   

                                                                 \
                                          2                   3   
(((readoutreceiver_0)))  0.000290-0.000252j -0.000126-0.000030j   
(((readoutreceiver_1)))  0.000404+0.000285j -0.000619-0.000269j   
(((readoutreceiver_2))) -0.000081+0.000279j  0.000265-0.000322j   
(((readoutreceiver_3))) -0.000009+0.000215j  0.000104+0.000032j   

                                                                 \
                                          4                   5   
(((readoutreceiver_0)))  0.000081+0.000200j  0.000281-0.000253j   
(((readoutreceiver_1))) -0.000079+0.000723j  0.000246+0.000136j   
(((readoutreceiver_2))) -0.000437-0.000284j -0.000292+0.000412j   
(((readoutreceiver_3))) -0.000207+0.000012j  0.000041+0.000437j   

                                                                 \
                                          6                   7   
(((readoutreceiver_0))) -0.000226-0.000165j  0.000205+0.000234j   
(((readoutreceiver_1))) -0.000124-0.000674j -0.000112+0.000165j   
(((readoutreceiver_2)))  0.000202-0.000232j -0.000108-0.000409j   
(((readoutreceiver_3)))  0.000226-0.000166j -0.000123-0.000006j   

                                                                 
                                          8                   9  
(((readoutreceiver_0)))  0.000370-0.000073j -0.000272-0.000114j  
(((readoutreceiver_1)))  0.000463-0.000247j -0.000024-0.000089j  
(((readoutreceiver_2)))  0.000152+0.000226j  0.000329-0.000201j  
(((readoutreceiver_3)))  0.000186+0.000372

In [8]:
df = program.get_iq_pandas(stack_channels=True)
channel0_rf_4_05_data = df["(rf, 4.05 GHz)"]["0"][digs[0]]
channel0_rf_4_05_data

(0.0023512427568418183-0.0026169676054433096j)

In [9]:
program.results.get_iq()[digs[0]]

array([[ 2.35124276e-03-2.61696761e-03j,  1.56245443e-03-3.16220147e-03j,
         1.99869235e-03-3.44414807e-03j,  2.33420904e-03-2.81241797e-03j,
         1.61864528e-03-3.17826601e-03j,  1.97415616e-03-3.32476444e-03j,
         2.24370314e-03-2.61436829e-03j,  1.58411493e-03-3.13454107e-03j,
         1.89427713e-03-3.38570377e-03j,  2.32488827e-03-2.75443529e-03j],
       [ 9.03837221e-03-1.31979863e-02j, -1.60448812e-02-1.15120579e-03j,
         6.88682387e-03+1.43951763e-02j,  9.14083963e-03-1.32208673e-02j,
        -1.60652258e-02-1.13517492e-03j,  6.92790761e-03+1.45518245e-02j,
         9.04989827e-03-1.29691433e-02j, -1.59535191e-02-1.09506675e-03j,
         7.00933728e-03+1.45844746e-02j,  9.11382591e-03-1.31389008e-02j],
       [-9.69921596e-02+1.41306446e-01j, -9.68726013e-02+1.41300715e-01j,
        -9.66008497e-02+1.41492925e-01j, -9.66862182e-02+1.41401766e-01j,
        -9.67742680e-02+1.41309223e-01j, -9.70541093e-02+1.41359629e-01j,
        -9.68253698e-02+1.41451627e-

In [10]:
xarray_data = program.get_iq_array()
xarray_data

<xarray.DataArray (channel: 4, rf: 5, shot: 10)> Size: 3kB
array([[[ 2.35124276e-03-2.61696761e-03j,
          1.56245443e-03-3.16220147e-03j,
          1.99869235e-03-3.44414807e-03j,
          2.33420904e-03-2.81241797e-03j,
          1.61864528e-03-3.17826601e-03j,
          1.97415616e-03-3.32476444e-03j,
          2.24370314e-03-2.61436829e-03j,
          1.58411493e-03-3.13454107e-03j,
          1.89427713e-03-3.38570377e-03j,
          2.32488827e-03-2.75443529e-03j],
        [ 9.03837221e-03-1.31979863e-02j,
         -1.60448812e-02-1.15120579e-03j,
          6.88682387e-03+1.43951763e-02j,
          9.14083963e-03-1.32208673e-02j,
         -1.60652258e-02-1.13517492e-03j,
          6.92790761e-03+1.45518245e-02j,
          9.04989827e-03-1.29691433e-02j,
         -1.59535191e-02-1.09506675e-03j,
          7.00933728e-03+1.45844746e-02j,
          9.11382591e-03-1.31389008e-02j],
...
        [ 6.18884111e-04+1.08999988e-02j,
         -9.91955269e-03-4.80722289e-03j,
          9.01942783e-03-6.14082153e-03j,
          7.96975201e-04+1.08534687e-02j,
         -9.74559262e-03-4.74106531e-03j,
          8.86968264e-03-6.14256811e-03j,
          8.93213455e-04+1.07568410e-02j,
         -1.00829324e-02-5.00753895e-03j,
          8.94359127e-03-6.09020717e-03j,
          7.95272045e-04+1.09735093e-02j],
        [-6.69431427e-05+2.27261535e-05j,
         -2.69320267e-04-8.14274398e-05j,
         -8.75962302e-06+2.15030159e-04j,
          1.03785371e-04+3.24787986e-05j,
         -2.06820091e-04+1.24558417e-05j,
          4.06028909e-05+4.36860893e-04j,
          2.26074919e-04-1.65653841e-04j,
         -1.22591191e-04-5.58106242e-06j,
          1.86249393e-04+3.71819284e-04j,
          1.36530683e-04-2.85289959e-05j]]])
Coordinates:
  * channel  (channel) <U17 272B 'readoutreceiver_0' ... 'readoutreceiver_3'
  * rf       (rf) float64 40B 4.05e+09 4.1e+09 4.15e+09 4.2e+09 4.25e+09
  * shot     (shot) int64 80B 0 1 2 3 4 5 6 7 8 9

In [11]:
xarray_data.sel(channel="readoutreceiver_0", rf=4.05e9, shot=0).values

array(0.00235124-0.00261697j)

In [12]:
xarray_data[0][0][0].values

array(0.00235124-0.00261697j)

In [13]:
print(xarray_data.sel(rf=[4.065e09, 4.09e09], method="nearest", tolerance=0.2e09))

<xarray.DataArray (channel: 4, rf: 2, shot: 10)> Size: 1kB
array([[[ 0.00235124-0.00261697j,  0.00156245-0.0031622j ,
          0.00199869-0.00344415j,  0.00233421-0.00281242j,
          0.00161865-0.00317827j,  0.00197416-0.00332476j,
          0.0022437 -0.00261437j,  0.00158411-0.00313454j,
          0.00189428-0.0033857j ,  0.00232489-0.00275444j],
        [ 0.00903837-0.01319799j, -0.01604488-0.00115121j,
          0.00688682+0.01439518j,  0.00914084-0.01322087j,
         -0.01606523-0.00113517j,  0.00692791+0.01455182j,
          0.0090499 -0.01296914j, -0.01595352-0.00109507j,
          0.00700934+0.01458447j,  0.00911383-0.0131389j ]],

       [[-0.00392558-0.0026286j , -0.00242739-0.00173962j,
         -0.00212863-0.00050826j, -0.00360018-0.00157223j,
         -0.00218814-0.00132137j, -0.00187957-0.00061227j,
         -0.00435733-0.00212076j, -0.00215927-0.00220587j,
         -0.0022505 -0.00061475j, -0.0041227 -0.00211136j],
        [ 0.01551049+0.00978542j,  0.00037847-0.018

In [14]:
xarray_data[
    :,
].values

array([[[ 2.35124276e-03-2.61696761e-03j,
          1.56245443e-03-3.16220147e-03j,
          1.99869235e-03-3.44414807e-03j,
          2.33420904e-03-2.81241797e-03j,
          1.61864528e-03-3.17826601e-03j,
          1.97415616e-03-3.32476444e-03j,
          2.24370314e-03-2.61436829e-03j,
          1.58411493e-03-3.13454107e-03j,
          1.89427713e-03-3.38570377e-03j,
          2.32488827e-03-2.75443529e-03j],
        [ 9.03837221e-03-1.31979863e-02j,
         -1.60448812e-02-1.15120579e-03j,
          6.88682387e-03+1.43951763e-02j,
          9.14083963e-03-1.32208673e-02j,
         -1.60652258e-02-1.13517492e-03j,
          6.92790761e-03+1.45518245e-02j,
          9.04989827e-03-1.29691433e-02j,
         -1.59535191e-02-1.09506675e-03j,
          7.00933728e-03+1.45844746e-02j,
          9.11382591e-03-1.31389008e-02j],
        [-9.69921596e-02+1.41306446e-01j,
         -9.68726013e-02+1.41300715e-01j,
         -9.66008497e-02+1.41492925e-01j,
         -9.66862182e-02+1.41401

In [15]:
xarray_data[:, [0, -1]].values

array([[[ 2.35124276e-03-2.61696761e-03j,
          1.56245443e-03-3.16220147e-03j,
          1.99869235e-03-3.44414807e-03j,
          2.33420904e-03-2.81241797e-03j,
          1.61864528e-03-3.17826601e-03j,
          1.97415616e-03-3.32476444e-03j,
          2.24370314e-03-2.61436829e-03j,
          1.58411493e-03-3.13454107e-03j,
          1.89427713e-03-3.38570377e-03j,
          2.32488827e-03-2.75443529e-03j],
        [-3.52554585e-04-2.42393203e-04j,
         -5.56220660e-05+3.56588658e-04j,
          2.89539537e-04-2.52136938e-04j,
         -1.25781980e-04-2.96531565e-05j,
          8.11054827e-05+2.00224330e-04j,
          2.81490092e-04-2.52850340e-04j,
         -2.25801394e-04-1.64635471e-04j,
          2.04950458e-04+2.34214862e-04j,
          3.69634580e-04-7.28241968e-05j,
         -2.71968595e-04-1.13773288e-04j]],

       [[-3.92558399e-03-2.62860430e-03j,
         -2.42738665e-03-1.73961819e-03j,
         -2.12862718e-03-5.08264336e-04j,
         -3.60017707e-03-1.572

In [16]:
program.plot_iq(channel_subplots=False)

In [17]:
new_frequencies = qcs.Array(
    "rfs", value=np.linspace(4.05e9, 4.25e9, num=20), dtype=float
)

program = make_program()
program.sweep(new_frequencies, frequency)

if run_on_hw:
    # initialize the backend pass
    # setting fpga_postprocessing=True enables hardware demodulation of trace data
    backend = qcs.HclBackend(channel_mapper=mapper, fpga_postprocessing=True)
    # the executor returns the program populated with results
    program = qcs.Executor(backend).execute(program)
    # (optional) export the data to an HDF5 file
    program.to_hdf5("program3.hdf5")

# we are loading a previously run program here for this example
program = qcs.load("program3.hdf5")

program.plot_iq(channel_subplots=False)

In [18]:
program.get_classified_pandas()

xarray_data = program.get_classified_array()
xarray_data

<xarray.DataArray (channel: 4, rf: 20, shot: 10)> Size: 6kB
array([[[1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 0, 0, 1, 0, 1, 1, 0, 1, 0],
        [1, 0, 1, 0, 1, 1, 0, 1, 0, 1],
        [0, 0, 0, 0, 0, 0, 0, 1, 1, 1],
        [1, 0, 1, 0, 1, 0, 1, 0, 1, 0],
        [1, 1, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 1, 0, 0, 1, 0, 1, 0, 0, 1],
        [1, 1, 1, 1, 0, 0, 0, 1, 1, 1],
        [1, 1, 0, 1, 1, 0, 1, 1, 0, 0],
        [0, 0, 1, 1, 0, 0, 1, 1, 0, 0],
        [0, 0, 0, 1, 1, 0, 0, 1, 1, 0],
        [1, 0, 0, 1, 0, 0, 1, 0, 0, 1],
        [0, 1, 1, 1, 1, 0, 0, 0, 1, 1],
        [0, 1, 0, 1, 0, 0, 1, 0, 1, 0],
        [1, 1, 1, 1, 1, 0, 0, 0, 0, 0],
        [0, 1, 0, 1, 0, 1, 0, 1, 0, 1],
        [1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
        [1, 1, 0, 1, 0, 1, 0, 1, 1, 0],
        [0, 0, 0, 1, 1, 1, 1, 0, 0, 0],
        [1, 0, 1, 1, 0, 1, 1, 0, 1, 1]],
...
       [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [1, 1, 0, 1, 0, 0, 1, 0, 1, 1],
        [0, 1, 0, 1, 1, 0, 1, 0, 1, 0],
        [1, 1, 1, 1, 1, 0, 0, 0, 0, 0],
        [0, 1, 0, 1, 0, 1, 0, 1, 0, 1],
        [0, 0, 0, 1, 1, 1, 1, 1, 1, 1],
        [1, 0, 1, 0, 0, 1, 0, 1, 0, 0],
        [1, 0, 0, 0, 1, 1, 1, 1, 0, 0],
        [0, 1, 1, 0, 0, 1, 0, 0, 1, 0],
        [1, 1, 0, 0, 1, 1, 1, 0, 0, 1],
        [1, 1, 0, 0, 1, 1, 1, 0, 0, 1],
        [0, 1, 1, 0, 0, 1, 0, 0, 1, 0],
        [1, 0, 0, 0, 1, 1, 1, 1, 0, 0],
        [1, 0, 1, 0, 0, 1, 0, 1, 0, 0],
        [0, 0, 0, 1, 1, 1, 1, 1, 1, 1],
        [1, 0, 0, 1, 0, 1, 0, 1, 0, 1],
        [1, 1, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 1, 0, 1, 1, 0, 1, 0, 1, 0],
        [1, 1, 1, 1, 0, 0, 0, 0, 1, 1],
        [1, 1, 0, 1, 1, 0, 1, 0, 0, 1]]])
Coordinates:
  * channel  (channel) <U17 272B 'readoutreceiver_0' ... 'readoutreceiver_3'
  * rf       (rf) float64 160B 4.05e+09 4.061e+09 ... 4.239e+09 4.25e+09
  * shot     (shot) int64 80B 0 1 2 3 4 5 6 7 8 9

In [19]:

print(xarray_data.sel(channel="readoutreceiver_0", rf=4.05e9))

<xarray.DataArray (shot: 10)> Size: 80B
array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])
Coordinates:
    channel  <U17 68B 'readoutreceiver_0'
    rf       float64 8B 4.05e+09
  * shot     (shot) int64 80B 0 1 2 3 4 5 6 7 8 9


In [20]:
xarray_data[0][0][0].values

array(1)

In [21]:
program.plot_classified(channel_subplots=False)

/home/kpclocal/jenkins/workspace/qcs_release_2025B/.venv3.10/lib/python3.10/site-packages/keysight/qcs/programs/program.py:1172: UserWarning:

get_classified() is deprecated and will be removed in a future version. Use get_classified_array() instead.



In [22]:
program = qcs.load("program4.hdf5")

In [23]:
program.plot_classified(avg=True, plot_type="2d")

/home/kpclocal/jenkins/workspace/qcs_release_2025B/.venv3.10/lib/python3.10/site-packages/keysight/qcs/programs/program.py:1172: UserWarning:

get_classified() is deprecated and will be removed in a future version. Use get_classified_array() instead.



In [24]:
program = make_program()

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# specify the amplitude values to be swept over
amplitudes = qcs.Array("amplitude", value=[0.2, 0.4, 0.6, 0.8, 1], dtype=float)

program.sweep(frequencies, frequency)
program.sweep(amplitudes, amplitude)

print(program.repetitions.items)

[Sweep(amp=Array(name=amplitude, shape=(5,), dtype=float, unit=none)), Sweep(rf=Array(name=frequencies, shape=(5,), dtype=float, unit=none)), Repeat(10)]


In [25]:
if run_on_hw:
    program = qcs.Executor(qcs.HclBackend(mapper, fpga_postprocessing=True)).apply(
        program
    )
    program.to_hdf5("program4.hdf5")

program = qcs.load("program4.hdf5")

program.get_iq_pandas(avg=True, stack_channels=True)

(amp, 0.2)                      \
                             (rf, 4.05 GHz)       (rf, 4.1 GHz)   
(((readoutreceiver_0)))  0.000054-0.000024j  0.000311-0.000175j   
(((readoutreceiver_1))) -0.000020-0.000008j  0.000115+0.000262j   
(((readoutreceiver_2)))  0.000079-0.000031j -0.000095+0.000329j   
(((readoutreceiver_3)))  0.000059-0.000005j -0.000145+0.000291j   

                                                                 \
                             (rf, 4.15 GHz)       (rf, 4.2 GHz)   
(((readoutreceiver_0))) -0.021990+0.030870j  0.000031-0.000342j   
(((readoutreceiver_1))) -0.032923-0.023555j  0.000313+0.000043j   
(((readoutreceiver_2))) -0.006091-0.037335j  0.000239+0.000210j   
(((readoutreceiver_3)))  0.001644-0.035483j  0.000079+0.000276j   

                                                     (amp, 0.4)  \
                             (rf, 4.25 GHz)      (rf, 4.05 GHz)   
(((readoutreceiver_0))) -0.000002+0.000011j  0.000237-0.000276j   
(((readoutreceiver_1))) -0.000088-0.000052j -0.000390-0.000342j   
(((readoutreceiver_2)))  0.000004+0.000044j  0.000433-0.000006j   
(((readoutreceiver_3))) -0.000008+0.000001j  0.000318+0.000171j   

                                                                 \
                              (rf, 4.1 GHz)      (rf, 4.15 GHz)   
(((readoutreceiver_0)))  0.000504-0.000323j -0.043212+0.060772j   
(((readoutreceiver_1)))  0.000282+0.000497j -0.065213-0.046224j   
(((readoutreceiver_2))) -0.000154+0.000612j -0.012199-0.073485j   
(((readoutreceiver_3))) -0.000201+0.000450j  0.002980-0.070049j   

                                                                 ...  \
                              (rf, 4.2 GHz)      (rf, 4.25 GHz)  ...   
(((readoutreceiver_0)))  0.000108-0.000541j -0.000025+0.000005j  ...   
(((readoutreceiver_1)))  0.000726-0.000080j -0.000004-0.000047j  ...   
(((readoutreceiver_2)))  0.000407+0.000504j -0.000023-0.000051j  ...   
(((readoutreceiver_3)))  0.000227+0.000548j -0.000059+0.000004j  ...   

                                 (amp, 0.8)                      \
                             (rf, 4.05 GHz)       (rf, 4.1 GHz)   
(((readoutreceiver_0)))  0.001422-0.001562j  0.000976-0.000823j   
(((readoutreceiver_1))) -0.002221-0.001783j  0.000929+0.001123j   
(((readoutreceiver_2)))  0.002674-0.000274j  0.000008+0.001391j   
(((readoutreceiver_3)))  0.001766+0.001234j -0.000320+0.001185j   

                                                                 \
                             (rf, 4.15 GHz)       (rf, 4.2 GHz)   
(((readoutreceiver_0))) -0.082690+0.117219j  0.000405-0.000960j   
(((readoutreceiver_1))) -0.127204-0.087077j  0.001139+0.000442j   
(((readoutreceiver_2))) -0.025622-0.140898j  0.000384+0.001028j   
(((readoutreceiver_3)))  0.003630-0.134825j  0.000308+0.000933j   

                                                       (amp, 1)  \
                             (rf, 4.25 GHz)      (rf, 4.05 GHz)   
(((readoutreceiver_0))) -0.000032+0.000049j  0.001917-0.003032j   
(((readoutreceiver_1))) -0.000023+0.000028j -0.002824-0.001579j   
(((readoutreceiver_2)))  0.000035+0.000039j  0.004332-0.001243j   
(((readoutreceiver_3)))  0.000031-0.000048j  0.003222+0.001599j   

                                                                 \
                              (rf, 4.1 GHz)      (rf, 4.15 GHz)   
(((readoutreceiver_0)))  0.000923-0.001317j -0.096898+0.141482j   
(((readoutreceiver_1)))  0.001513+0.001036j -0.154821-0.102813j   
(((readoutreceiver_2)))  0.000439+0.001622j -0.033850-0.169222j   
(((readoutreceiver_3))) -0.000203+0.001572j  0.002406-0.164136j   

                                                                 
                              (rf, 4.2 GHz)      (rf, 4.25 GHz)  
(((readoutreceiver_0)))  0.000648-0.000950j  0.000026-0.000017j  
(((readoutreceiver_1)))  0.001006+0.000709j -0.000158-0.000085j  
(((readoutreceiver_2)))  0.000125+0.001070j  0.000024-0.000145j  
(((readoutreceiver_3)))  0.000017+0.001130j -0

In [26]:
# plot over amplitude for each frequency
program.plot_iq(channel_subplots=False)

In [27]:
# plot over frequency for each amplitude
program.plot_iq(channel_subplots=False, plot_axis=1)

In [28]:
program = make_program()

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# specify the amplitude values to be swept over
amplitudes = qcs.Array("amplitude", value=[0.2, 0.4, 0.6, 0.8, 1], dtype=float)

program.sweep([frequencies, amplitudes], [frequency, amplitude])

Program([Layer(Channels(labels=[0, 1], name=readoutawg, absolute_phase=False)=[RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=_implicit, value=1.0, dtype=float, unit=none)}, rf_frequency=Scalar(name=rf, value=None, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))], Channels(labels=[0, 1], name=readoutreceiver, absolute_phase=False)=[Acquisition(IntegrationFilter(RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=_implicit, value=1.0, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4150000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, un

In [29]:
if run_on_hw:
    program = qcs.Executor(qcs.HclBackend(mapper, fpga_postprocessing=True)).apply(
        program
    )
    program.to_hdf5("program5.hdf5")

program = qcs.load("program5.hdf5")

program.get_iq_pandas(avg=True, stack_channels=True)

(rf, 4.05 GHz), (amp, 0.2)  \
(((readoutreceiver_0)))          0.000012-0.000053j   
(((readoutreceiver_1)))          0.000023+0.000026j   
(((readoutreceiver_2)))          0.000061-0.000079j   
(((readoutreceiver_3)))          0.000015+0.000015j   

                         (rf, 4.1 GHz), (amp, 0.4)  \
(((readoutreceiver_0)))         0.000591-0.000309j   
(((readoutreceiver_1)))         0.000343+0.000561j   
(((readoutreceiver_2)))        -0.000158+0.000644j   
(((readoutreceiver_3)))        -0.000241+0.000522j   

                         (rf, 4.15 GHz), (amp, 0.6)  \
(((readoutreceiver_0)))         -0.062908+0.089234j   
(((readoutreceiver_1)))         -0.096364-0.067022j   
(((readoutreceiver_2)))         -0.018962-0.107608j   
(((readoutreceiver_3)))          0.003421-0.102856j   

                         (rf, 4.2 GHz), (amp, 0.8)  (rf, 4.25 GHz), (amp, 1)  
(((readoutreceiver_0)))         0.000409-0.000950j       -0.000002-0.000024j  
(((readoutreceiver_1)))         0.000932+0.000280j       -0.000066-0.000098j  
(((readoutreceiver_2)))         0.000361+0.000904j       -0.000002-0.000001j  
(((readoutreceiver_3)))         0.000300+0.000922j        0.000002+0.000000j

In [30]:
# plot the results
program.plot_iq(channel_subplots=False)

In [31]:
frequency = qcs.Scalar("rf", dtype=float)

"""Creates a simple program with a single RF waveform"""
program = qcs.Program()
# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, frequency)
program.add_waveform(gauss, awgs)

# define an integration filter using the same RF waveform but with fixed frequency
int_filter = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, 4.15e9)
program.add_acquisition(int_filter, digs)

# specify the frequency values to be swept over
frequencies = qcs.Array(
    "frequencies", value=[4.05e9, 4.1e9, 4.15e9, 4.2e9, 4.25e9], dtype=float
)

# add the sweep, targeting the `frequency` variable
program.sweep(frequencies, frequency)

# specify the number of shots
program.n_shots(10)

program.draw()

In [32]:
program.repetitions.hw_items

[Repeat(10),
 Sweep(rf=Array(name=frequencies, shape=(5,), dtype=float, unit=none))]

In [33]:
amplitude = qcs.Scalar("amp", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude, 4e9)
program.add_waveform(gauss, awgs)

# define the values for the sweep
amplitudes = qcs.Array("amplitudes", value=np.linspace(0.1, 0.2, 10000), dtype=float)

# sweep the program
program.sweep(amplitudes, amplitude)
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))])])

In [34]:
frequency = qcs.Scalar("rf", dtype=float)
amplitude = qcs.Scalar("amp", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude, frequency)
program.add_waveform(gauss, awgs)

# define the values for each sweep
frequencies = qcs.Array(
    "frequencies", value=np.linspace(4e9, 4.1e9, 10000), dtype=float
)
amplitudes = qcs.Array("amplitudes", value=np.linspace(0.1, 0.2, 10000), dtype=float)

# sweep the program
program.sweep(frequencies, frequency)
program.sweep(amplitudes, amplitude)
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=rf, value=None, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))])])

In [35]:
amplitude1 = qcs.Scalar("amp", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude, 4e9)
program.add_waveform(gauss, awgs)
program.add_waveform(gauss, awgs, pre_delay=20e-9)
program.add_waveform(gauss, awgs, pre_delay=20e-9)
# define the values for the sweep
amplitudes = qcs.Array("amplitudes", value=np.linspace(0.1, 0.2, 10000), dtype=float)

# sweep the program
program.sweep(amplitudes, amplitude)
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)), Delay(Scalar(name=_implicit, value=2e-08, dtype=float, unit=s)), RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)), Delay(Scalar(name=_implicit, value=2e-08, dtype=float, unit=s)), RFWaveform(duratio

In [36]:
amplitude1 = qcs.Scalar("amp1", dtype=float)
amplitude2 = qcs.Scalar("amp2", dtype=float)

program = qcs.Program()

# define the waveform using this frequency variable & add it to the program
gauss1 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude1, 4e9)
gauss2 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), amplitude2, 4e9)
program.add_waveform(gauss1, awgs)
program.add_waveform(gauss2, awgs)

# define the values for the sweep
amplitudes1 = qcs.Array("amplitudes1", value=np.linspace(0.1, 0.2, 10000), dtype=float)
amplitudes2 = qcs.Array("amplitudes2", value=np.linspace(0.3, 0.4, 10000), dtype=float)

# sweep the program
program.sweep([amplitudes1, amplitudes2], [amplitude1, amplitude2])
program.n_shots(10)

Program([Layer([RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp1, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)), RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=amp2, value=None, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4000000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))])])